In [1]:
import numpy as np
import random

import torch
import torch.nn as nn
import torch.nn.functional as func
import torch.optim as optim

from matplotlib import pyplot as plt

from numpy import exp,arange
from pylab import meshgrid,cm,imshow,contour,clabel,colorbar,axis,title,show

In [2]:
# ==========
# helping methods
# ==========

# generate a list from lower and upper bound
def gen_list(p0, pn, delta, dig=5):
    ret = []
    i = p0
    while i < pn:
        ret.append(float(i))
        i += delta
        i = round(i, dig)
    return ret

# padding and zero padding
def padding(origin, a_list, b_list):
    return np.hstack((a_list, origin, b_list))

def zero_padding(origin, num):
    zero_list = [0 for i in range(num)]
    return padding(origin, zero_list, zero_list)

# trainning pairs
def gen_pair(u, x, t, length=3, num=1000):
    pairs = []
    for i in range(num):
        r = random.randint(0, t-2)
        current_t = u[r]
        next_t = u[r+1]
        p = random.randint(length, x-1-length)
        train = current_t[p-length:p+length+1]
        solu = next_t[p]
        pair = {'input': train, 'solu': solu}
        pairs.append(pair)
    return pairs

# trainning pairs (in average)
def gen_pair_ave(u, x, t, length=3, num=1000):
    pairs = []
    for i in range(num):
        r = random.randint(0, t-2)
        current_t = u[r]
        next_t = u[r+1]
        p = random.randint(length, x-2-length)
        train0 = current_t[p-length:p+length+2]
        solu1 = next_t[p]
        solu2 = next_t[p+1]
        train = []
        for j in range(len(train0)-1):
                train.append(0.5 * (train0[j] + train0[j+1]))
        solu = 0.5 * (solu1 + solu2)
        pair = {'input': train, 'solu': solu}
        pairs.append(pair)
    return pairs

In [3]:
# the analytical representation of exact solution
def heat_equ_analytical_solu(x, t):
    return np.sin(np.pi * x) * np.exp(-np.power(np.pi, 2) * t)

In [4]:
# restnet
class ResNet(nn.Module):
    def __init__(self, i, h, o):
        super(ResNet, self).__init__()
        self.linear1 = nn.Linear(i, h)
        self.relu1 = nn.ReLU()
        self.linear2 = nn.Linear(h, o)
        self.relu2 = nn.ReLU()
        
    def forward(self, x):
        out = self.linear1(x)
        out = self.relu1(out)
        out = self.linear2(out)
        out = self.relu2(out)
        return out + torch.mean(x)

    def load_model(self, save_path):
        self.load_state_dict(torch.load(save_path))

    def save_model(self, save_path):
        torch.save(self.state_dict(), save_path)

## $\Delta x=\frac{1}{20}$ $\Delta t=\frac{1}{80}$

In [5]:
x_1 = arange(0, 2 * np.pi, 1/20)
t_1 = arange(0, 2 * np.pi, 1/80)
X_1,T_1 = meshgrid(x_1, t_1) # grid of point
Z_1 = heat_equ_analytical_solu(X_1, T_1) # evaluation of the function on the grid

In [6]:
# preparing the trainning set
data_pairs_1 = gen_pair_ave(Z_1, len(Z_1[0]), len(Z_1), length=3, num=10000)
print(data_pairs_1)

[{'input': [1.7378229976168235e-14, 2.848786793562076e-14, 3.889604004068504e-14, 4.834646255139177e-14, 5.6606434701373185e-14, 6.347256856302083e-14, 6.877579713326914e-14], 'solu': 4.273520274506385e-14}, {'input': [-1.4452273888651412e-10, 1.445227388865123e-10, 4.300095871846847e-10, 7.049081723263705e-10, 9.624495788092809e-10, 1.1962922824748868e-09, 1.4006782998795005e-09], 'solu': 6.230940604805996e-10}, {'input': [4.3806641187994015e-10, 4.042875767666782e-10, 3.605538397598796e-10, 3.07942070608603e-10, 2.477477456778036e-10, 1.8145304902078912e-10, 1.1069037608873949e-10], 'solu': 2.7220123514113477e-10}, {'input': [-5.9306529635665155e-18, -6.943902449155906e-18, -7.786170010956101e-18, -8.4367162262698e-18, -8.879522488236881e-18, -9.103685437097993e-18, -9.103685437097991e-18], 'solu': -7.457521386367323e-18}, {'input': [-1.5405916476286106e-05, -2.525468443020407e-05, -3.448159823795812e-05, -4.285946065923007e-05, -5.018198091667697e-05, -5.626885425950902e-05, -6.0970

In [7]:
model_1 = ResNet(7, 6, 1)
optimizer_1 = optim.Adam(model_1.parameters(), lr=0.001, betas=(0.9, 0.999), eps=1e-08, weight_decay=0, amsgrad=False)
criterion_1 = nn.MSELoss()
model_1.train()

ResNet(
  (linear1): Linear(in_features=7, out_features=6, bias=True)
  (relu1): ReLU()
  (linear2): Linear(in_features=6, out_features=1, bias=True)
  (relu2): ReLU()
)

In [8]:
list_of_loss_1 = []
list_of_output_1 = []
for data in data_pairs_1:
    output = model_1(torch.FloatTensor(data["input"]))
    loss = criterion_1(output, torch.FloatTensor([data["solu"]]))
    list_of_loss_1.append(np.log10(loss.item()))
    list_of_output_1.append(output)
    model_1.zero_grad()
    loss.backward()
    optimizer_1.step()

<ipython-input-8-ac38450c9edb>:6: RuntimeWarning: divide by zero encountered in log10
  list_of_loss_1.append(np.log10(loss.item()))


In [9]:
list_of_loss_1_file = open('list_of_loss_13.txt', 'w+')
for value in list_of_loss_1:
    list_of_loss_1_file.write(str(value)+" ")
list_of_loss_1_file.close()

list_of_output_1_file = open('list_of_output_13.txt', 'w+')
for value in list_of_output_1:
    list_of_output_1_file.write(str(value)+" ")
list_of_output_1_file.close()

In [10]:
model_1.save_model("model_1 delta x=1 20 delta t=1 80")

## $\Delta x=\frac{1}{40}$ $\Delta t=\frac{1}{80}$

In [11]:
x_2 = arange(0, 2 * np.pi, 1/40)
t_2 = arange(0, 2 * np.pi, 1/80)
X_2,T_2 = meshgrid(x_2, t_2) # grid of point
Z_2 = heat_equ_analytical_solu(X_2, T_2) # evaluation of the function on the grid

In [12]:
# preparing the trainning set
data_pairs_2 = gen_pair_ave(Z_2, len(Z_2[0]), len(Z_2), length=3, num=10000)
print(data_pairs_2)

[{'input': [-1.4554419458366275e-07, -1.1414225576347147e-07, -8.203659198034707e-08, -4.942514532772875e-08, -1.6508976218636367e-08, 1.6508976218635957e-08, 4.942514532772834e-08], 'solu': -4.368868981964299e-08}, {'input': [0.0002006243471534839, 0.00020062434715348388, 0.00019938743133891736, 0.00019692122570709735, 0.00019324093523584055, 0.00018836925013972317, 0.0001823362059773624], 'solu': 0.00017406585841629589}, {'input': [-1.7408911222955256e-20, -1.798492809060767e-20, -1.8450061895986036e-20, -1.8801444934507477e-20, -1.9036910812892798e-20, -1.915500780570141e-20, -1.9155007805701404e-20], 'solu': -1.661928337202013e-20}, {'input': [5.333384160222376e-13, 6.224636754125599e-13, 7.077512392537873e-13, 7.886752813538457e-13, 8.647368780832136e-13, 9.354670844050066e-13, 1.0004298250770709e-12], 'solu': 6.971388653895805e-13}, {'input': [-6.155598776739765e-06, -3.7086055962982364e-06, -1.2387476291190257e-06, 1.2387476291190352e-06, 3.708605596298246e-06, 6.155598776739774

In [13]:
model_2 = ResNet(7, 6, 1)
optimizer_2 = optim.Adam(model_2.parameters(), lr=0.001, betas=(0.9, 0.999), eps=1e-08, weight_decay=0, amsgrad=False)
criterion_2 = nn.MSELoss()
model_2.train()

ResNet(
  (linear1): Linear(in_features=7, out_features=6, bias=True)
  (relu1): ReLU()
  (linear2): Linear(in_features=6, out_features=1, bias=True)
  (relu2): ReLU()
)

In [14]:
list_of_loss_2 = []
list_of_output_2 = []
for data in data_pairs_2:
    output = model_2(torch.FloatTensor(data["input"]))
    loss = criterion_2(output, torch.FloatTensor([data["solu"]]))
    list_of_loss_2.append(np.log10(loss.item()))
    list_of_output_2.append(output)
    model_2.zero_grad()
    loss.backward()
    optimizer_2.step()

<ipython-input-14-de329c128c88>:6: RuntimeWarning: divide by zero encountered in log10
  list_of_loss_2.append(np.log10(loss.item()))


In [15]:
list_of_loss_2_file = open('list_of_loss_23.txt', 'w+')
for value in list_of_loss_2:
    list_of_loss_2_file.write(str(value)+" ")
list_of_loss_2_file.close()

list_of_output_2_file = open('list_of_output_23.txt', 'w+')
for value in list_of_output_2:
    list_of_output_2_file.write(str(value)+" ")
list_of_output_2_file.close()

In [16]:
model_2.save_model("model_1 delta x=1 40 delta t=1 80")

## $\Delta x=\frac{1}{80}$ $\Delta t=\frac{1}{80}$

In [17]:
x_3 = arange(0, 2 * np.pi, 1/80)
t_3 = arange(0, 2 * np.pi, 1/80)
X_3,T_3 = meshgrid(x_3, t_3) # grid of point
Z_3 = heat_equ_analytical_solu(X_3, T_3) # evaluation of the function on the grid

In [18]:
# preparing the trainning set
data_pairs_3 = gen_pair_ave(Z_3, len(Z_3[0]), len(Z_3), length=3, num=10000)
print(data_pairs_3)

[{'input': [-6.833476180380356e-17, -6.710859294369521e-17, -6.57789474973955e-17, -6.434787568180803e-17, -6.28175841059463e-17, -6.119043236850249e-17, -5.946892941951748e-17], 'solu': -5.68794358129736e-17}, {'input': [-0.01640141852140917, -0.01711339734146207, -0.017798988543218187, -0.018457134994737116, -0.01908682188189402, -0.019687078273149458, -0.020256978616655576], 'solu': -0.016314935250012392}, {'input': [-6.439744741126305e-17, -6.490251078701788e-17, -6.530749919536696e-17, -6.561178817353875e-17, -6.581490852998422e-17, -6.591654706783619e-17, -6.591654706783619e-17], 'solu': -5.799665419329945e-17}, {'input': [-7.917544794566817e-27, -9.10264794773963e-27, -1.0273715477550116e-26, -1.1428941682747999e-26, -1.25665452882573e-26, -1.368477219177348e-26, -1.478189816846202e-26], 'solu': -1.0102458674294221e-26}, {'input': [-1.4278172830085282e-06, -1.3218433807869775e-06, -1.213831291881375e-06, -1.1039475631039388e-06, -9.923616271999068e-07, -8.792455415945406e-07, -7

In [19]:
model_3 = ResNet(7, 6, 1)
optimizer_3 = optim.Adam(model_3.parameters(), lr=0.001, betas=(0.9, 0.999), eps=1e-08, weight_decay=0, amsgrad=False)
criterion_3 = nn.MSELoss()
model_3.train()

ResNet(
  (linear1): Linear(in_features=7, out_features=6, bias=True)
  (relu1): ReLU()
  (linear2): Linear(in_features=6, out_features=1, bias=True)
  (relu2): ReLU()
)

In [20]:
list_of_loss_3 = []
list_of_output_3 = []
for data in data_pairs_3:
    output = model_3(torch.FloatTensor(data["input"]))
    loss = criterion_3(output, torch.FloatTensor([data["solu"]]))
    list_of_loss_3.append(np.log10(loss.item()))
    list_of_output_3.append(output)
    model_3.zero_grad()
    loss.backward()
    optimizer_3.step()

<ipython-input-20-3f959fb14d49>:6: RuntimeWarning: divide by zero encountered in log10
  list_of_loss_3.append(np.log10(loss.item()))


In [21]:
list_of_loss_3_file = open('list_of_loss_33.txt', 'w+')
for value in list_of_loss_3:
    list_of_loss_3_file.write(str(value)+" ")
list_of_loss_3_file.close()

list_of_output_3_file = open('list_of_output_33.txt', 'w+')
for value in list_of_output_3:
    list_of_output_3_file.write(str(value)+" ")
list_of_output_3_file.close()

In [22]:
model_3.save_model("model_1 delta x=1 80 delta t=1 80")

## $\Delta x=\frac{1}{160}$ $\Delta t=\frac{1}{80}$

In [23]:
x_4 = arange(0, 2 * np.pi, 1/160)
t_4 = arange(0, 2 * np.pi, 1/80)
X_4,T_4 = meshgrid(x_4, t_4) # grid of point
Z_4 = heat_equ_analytical_solu(X_4, T_4) # evaluation of the function on the grid

In [24]:
# preparing the trainning set
data_pairs_4 = gen_pair_ave(Z_4, len(Z_4[0]), len(Z_4), length=3, num=10000)
print(data_pairs_4)

[{'input': [1.3062107428299365e-14, 1.417598323448625e-14, 1.5284393929284063e-14, 1.63869121992704e-14, 1.7483113002664876e-14, 1.8572573733190556e-14, 1.9654874382996987e-14], 'solu': 1.448498976439018e-14}, {'input': [-1.027223779454912e-07, -1.0087463851503284e-07, -9.898800999119042e-08, -9.706321970517329e-08, -9.510100970027695e-08, -9.310213644581067e-08, -9.106737054546452e-08], 'solu': -8.57977224037843e-08}, {'input': [2.5676246846173487e-11, 2.6030053423319286e-11, 2.6373824919365677e-11, 2.6707428803856946e-11, 2.7030736466145176e-11, 2.7343623264972107e-11, 2.7645968576520726e-11], 'solu': 2.3607671058020932e-11}, {'input': [0.025133050435332698, 0.0269459876975916, 0.028748536768652796, 0.0305400027315363, 0.03231969494201127, 0.03408692729485245, 0.03584101848834717], 'solu': 0.026995423029754634}, {'input': [9.563910129053183e-15, 1.0557026773053125e-14, 1.1546073482269864e-14, 1.253066896036963e-14, 1.3510433627052984e-14, 1.4484989764390247e-14, 1.5453961662438952e-1

In [25]:
model_4 = ResNet(7, 6, 1)
optimizer_4 = optim.Adam(model_4.parameters(), lr=0.001, betas=(0.9, 0.999), eps=1e-08, weight_decay=0, amsgrad=False)
criterion_4 = nn.MSELoss()
model_4.train()

ResNet(
  (linear1): Linear(in_features=7, out_features=6, bias=True)
  (relu1): ReLU()
  (linear2): Linear(in_features=6, out_features=1, bias=True)
  (relu2): ReLU()
)

In [26]:
list_of_loss_4 = []
list_of_output_4 = []
for data in data_pairs_4:
    output = model_4(torch.FloatTensor(data["input"]))
    loss = criterion_4(output, torch.FloatTensor([data["solu"]]))
    list_of_loss_4.append(np.log10(loss.item()))
    list_of_output_4.append(output)
    model_4.zero_grad()
    loss.backward()
    optimizer_4.step()

<ipython-input-26-f52da78e2a74>:6: RuntimeWarning: divide by zero encountered in log10
  list_of_loss_4.append(np.log10(loss.item()))


In [27]:
list_of_loss_4_file = open('list_of_loss_43.txt', 'w+')
for value in list_of_loss_4:
    list_of_loss_4_file.write(str(value)+" ")
list_of_loss_4_file.close()

list_of_output_4_file = open('list_of_output_43.txt', 'w+')
for value in list_of_output_4:
    list_of_output_4_file.write(str(value)+" ")
list_of_output_4_file.close()

In [28]:
model_4.save_model("model_1 delta x=1 160 delta t=1 80")